# Assembler rubustness - Contiguity

## Imports

In [7]:
import sys
from plotly.offline import plot
import glob
import fnmatch
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import json
import pandas as pd
from itertools import groupby
import csv
import numpy as np
from statistics import mean

## Global variables

In [3]:
METRICS_COLUMNS_GLOBAL = ['run','sample','assembler', 'contigs', 'basepairs', 'max_contig', 'Ns', 'n50', 'misassemblies', 'mapped_reads']
ASSEMBLER_PROCESS_LIST = ["BCALM2", "GATBMINIAPIPELINE", "MINIA", "MEGAHIT", "METASPADES", "UNICYCLER", "SPADES",
                          "SKESA", "VELVETOPTIMIZER", "IDBA"]
PROCESS_TO_NAME = {"BCALM2": "BCALM2", 
                   "GATBMINIAPIPELINE": "GATBMiniaPipeline",
                   "MINIA": "MINIA",
                   "MEGAHIT": "MEGAHIT", 
                   "METASPADES": "metaSPAdes", 
                   "UNICYCLER": "Unicycler", 
                   "SPADES": "SPAdes",
                    "SKESA": "SKESA",
                   "VELVETOPTIMIZER": "VelvetOptimizer",
                   "IDBA": "IDBA-UD"}
log_distributed = ['LHS', 'LNN', 'ERR2935805']
even_distribution = ['EHS', 'LNN', 'ERR2984773']
COLOURS = ['#004B93', "#009392", "#39B185", "#9CCB86", "#E9E29C", "#EEB479", "#E88471","#CF597E",'lightgray', 'darkgray']

## Lx Metric

### Load data

In [4]:
_files = glob.glob('../Results/*/results/*/stats/*_lx.csv')

df_list = []
for f in _files:
    run = f.split('/')[-5]
    sample = f.split('/')[-3]
    assembler = f.split('/')[-1].split('_')[1]
    df = pd.read_csv(f)
    df['run'] = run
    df['Sample'] = sample
    df['Assembler'] = assembler
    df_list.append(df)

df = pd.concat(df_list)
df['distribution'] = np.where(df['Sample'].isin(log_distributed), 'Log', 'Even')
df

Unnamed: 0                       Reference Assembler        Lx  nContigs  \
0             0               Bacillus_subtilis    SPAdes  0.000000       0.0   
1             1               Bacillus_subtilis    SPAdes  0.111111       0.0   
2             2               Bacillus_subtilis    SPAdes  0.222222       1.0   
3             3               Bacillus_subtilis    SPAdes  0.333333       2.0   
4             4               Bacillus_subtilis    SPAdes  0.444444       4.0   
..          ...                             ...       ...       ...       ...   
115         115  Staphylococcus_aureus_plasmid3     SKESA  0.555556       0.0   
116         116  Staphylococcus_aureus_plasmid3     SKESA  0.666667       0.0   
117         117  Staphylococcus_aureus_plasmid3     SKESA  0.777778       0.0   
118         118  Staphylococcus_aureus_plasmid3     SKESA  0.888889       0.0   
119         119  Staphylococcus_aureus_plasmid3     SKESA  1.000000       NaN   

      run      Sample distribution  
0    run1         LNN          Log  
1    run1         LNN          Log  
2    run1         LNN          Log  
3    run1         LNN          Log  
4    run1         LNN          Log  
..    ...         ...          ...  
115  run2  ERR2984773         Even  
116  run2  ERR2984773         Even  
117  run2  ERR2984773         Even  
118  run2  ERR2984773         Even  
119  run2  ERR2984773         Even  

[20520 rows x 8 columns]

### Create Average, Upper bound and Lower bound variables for plot

In [23]:
plot_df = pd.DataFrame(columns=['Reference', 'Assembler', 'Sample', "Average", "Upper bound", "Lower bound", 'Lx'])

for sample in sorted(df['Sample'].unique(), key=lambda v: v.upper(), reverse=True):
    for reference in sorted(df['Reference'].unique(), key=lambda v: v.upper(), reverse=True):
        for assembler in sorted(df['Assembler'].unique(), key=lambda v: v.upper(), reverse=True):
            for x in df['Lx'].unique():
                contigs = list(df['nContigs'][(df['Assembler'] == assembler) & (df['Reference'] == reference) & (df['Sample'] == sample) & (df['Lx'] == x)])
                if contigs:
                    avg = mean(contigs) if len(set(contigs)) > 1 else contigs[0]
                    upper_bound = max(contigs)
                    lower_bound = min(contigs)
                    plot_df = plot_df.append({'Reference':reference, 'Assembler': assembler, 'Sample': sample, "Average": avg, "Upper bound": upper_bound, "Lower bound": lower_bound, 'Lx': x}, ignore_index=True)

plot_df

Reference  Assembler Sample  Average  Upper bound  \
0     Staphylococcus_aureus_plasmid3  Unicycler    LNN      0.0          0.0   
1     Staphylococcus_aureus_plasmid3  Unicycler    LNN      0.0          0.0   
2     Staphylococcus_aureus_plasmid3  Unicycler    LNN      0.0          0.0   
3     Staphylococcus_aureus_plasmid3  Unicycler    LNN      0.0          0.0   
4     Staphylococcus_aureus_plasmid3  Unicycler    LNN      0.0          0.0   
...                              ...        ...    ...      ...          ...   
6835               Bacillus_subtilis     BCALM2    EHS   1000.0       1000.0   
6836               Bacillus_subtilis     BCALM2    EHS   1374.0       1374.0   
6837               Bacillus_subtilis     BCALM2    EHS      NaN          NaN   
6838               Bacillus_subtilis     BCALM2    EHS      NaN          NaN   
6839               Bacillus_subtilis     BCALM2    EHS      NaN          NaN   

      Lower bound        Lx  
0             0.0  0.000000  
1             0.0  0.111111  
2             0.0  0.222222  
3             0.0  0.333333  
4             0.0  0.444444  
...           ...       ...  
6835       1000.0  0.555556  
6836       1374.0  0.666667  
6837          NaN  0.777778  
6838          NaN  0.888889  
6839          NaN  1.000000  

[6840 rows x 7 columns]

### Plot data

In [35]:
for sample in sorted(plot_df['Sample'].unique(), key=lambda v: v.upper(), reverse=True):
    print('-' + sample)
    fig=make_subplots(rows=6, cols=2, column_titles=sorted(df['Reference'].unique(), key=lambda v: v.upper(), reverse=True),
                     shared_yaxes=True, shared_xaxes=True, x_title="Lx", y_title="Contigs")
    row=1
    col=1
    for reference in sorted(plot_df['Reference'].unique(), key=lambda v: v.upper(), reverse=True):
        print('--' + reference)
        i=0
        print(row, col)
        for assembler in sorted(plot_df['Assembler'].unique(), key=lambda v: v.upper(), reverse=True):
            print('---' + assembler)
            showlegend=True if col==1 and row==1 else False
            x = list(plot_df['Lx'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
            if x:
                y=list(plot_df['Average'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
                up_bound=list(plot_df['Upper bound'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
                low_bound=list(plot_df['Lower bound'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])

                fig.add_trace(go.Scatter(name=assembler,
                                         x=x,
                                         y=y,
                                         mode='lines',
                                         line=dict(color=COLOURS[i]),
                                         showlegend=showlegend), col=col, row=row)
                fig.add_trace(go.Scatter(name='Upper Bound',
                                         x=x,
                                         y=up_bound,
                                         mode='lines',
                                         marker=dict(color=COLOURS[i]),line=dict(width=0),showlegend=False),col=col, row=row)
                fig.add_trace(go.Scatter(name='Lower Bound',
                                         x=x,
                                         y=low_bound,
                                         marker=dict(color=COLOURS[i]),
                                         line=dict(width=0),
                                         mode='lines',
                                         fillcolor=COLOURS[i],
                                         fill='tonexty',showlegend=False),col=col, row=row)
            i+=1
        if col == 2:
            col = 1
            row += 1
        else:
            col += 1
    fig.update_layout(plot_bgcolor='rgb(255,255,255)', title="{} Lx metric variation".format(sample))
    fig.update_xaxes(showline=True, linewidth=1, linecolor='#DCDCDC', gridcolor='#DCDCDC', rangemode='tozero')
    fig.update_yaxes(showline=True, linewidth=1, linecolor='#DCDCDC', gridcolor='#DCDCDC', range=[0, 1])
    for i in fig['layout']['annotations']:
        i['font']['size'] = 12
    fig.show()
    plot(fig, filename='Plots/Contiguity/Lx/{}.html'.format(sample), auto_open=False)

-LNN
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---VelvetO

-LHS
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---VelvetO

-ERR2984773
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---

-ERR2935805
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---

-ENN
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---VelvetO

-EHS
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---VelvetO

## NAx Metric

### Load data

In [36]:
_files = glob.glob('../Results/*/results/*/stats/*nax.csv')

df_list = []
for f in _files:
    run = f.split('/')[-5]
    sample = f.split('/')[-3]
    assembler = f.split('/')[-1].split('_')[1]
    df = pd.read_csv(f)
    df['run'] = run
    df['Sample'] = sample
    df['Assembler'] = assembler
    df_list.append(df)

df = pd.concat(df_list)
df['distribution'] = np.where(df['Sample'].isin(log_distributed), 'Log', 'Even')
df

Unnamed: 0                       Reference   Assembler       NAx  \
0             0               Bacillus_subtilis   Unicycler  0.000000   
1             1               Bacillus_subtilis   Unicycler  0.111111   
2             2               Bacillus_subtilis   Unicycler  0.222222   
3             3               Bacillus_subtilis   Unicycler  0.333333   
4             4               Bacillus_subtilis   Unicycler  0.444444   
..          ...                             ...         ...       ...   
115         115  Staphylococcus_aureus_plasmid3  metaSPAdes  0.555556   
116         116  Staphylococcus_aureus_plasmid3  metaSPAdes  0.666667   
117         117  Staphylococcus_aureus_plasmid3  metaSPAdes  0.777778   
118         118  Staphylococcus_aureus_plasmid3  metaSPAdes  0.888889   
119         119  Staphylococcus_aureus_plasmid3  metaSPAdes  1.000000   

     Basepairs   run      Sample distribution  
0       768201  run1         LNN          Log  
1       768201  run1         LNN          Log  
2       768201  run1         LNN          Log  
3       768201  run1         LNN          Log  
4       768201  run1         LNN          Log  
..         ...   ...         ...          ...  
115       3857  run2  ERR2984773         Even  
116       3857  run2  ERR2984773         Even  
117       3857  run2  ERR2984773         Even  
118       3857  run2  ERR2984773         Even  
119       3857  run2  ERR2984773         Even  

[20520 rows x 8 columns]

### Create Average, Upper bound and Lower bound variables for plot

In [40]:
plot_df = pd.DataFrame(columns=['Reference', 'Assembler', 'Sample', "Average", "Upper bound", "Lower bound", 'NAx'])

for sample in sorted(df['Sample'].unique(), key=lambda v: v.upper(), reverse=True):
    for reference in sorted(df['Reference'].unique(), key=lambda v: v.upper(), reverse=True):
        for assembler in sorted(df['Assembler'].unique(), key=lambda v: v.upper(), reverse=True):
            for x in df['NAx'].unique():
                contigs = list(df['Basepairs'][(df['Assembler'] == assembler) & (df['Reference'] == reference) & (df['Sample'] == sample) & (df['NAx'] == x)])
                if contigs:
                    avg = mean(contigs) if len(set(contigs)) > 1 else contigs[0]
                    upper_bound = max(contigs)
                    lower_bound = min(contigs)
                    plot_df = plot_df.append({'Reference':reference, 'Assembler': assembler, 'Sample': sample, "Average": avg, "Upper bound": upper_bound, "Lower bound": lower_bound, 'NAx': x}, ignore_index=True)

plot_df

Reference  Assembler Sample Average Upper bound  \
0     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
1     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
2     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
3     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
4     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
...                              ...        ...    ...     ...         ...   
6835               Bacillus_subtilis     BCALM2    EHS    1852        1852   
6836               Bacillus_subtilis     BCALM2    EHS    1638        1638   
6837               Bacillus_subtilis     BCALM2    EHS    1413        1413   
6838               Bacillus_subtilis     BCALM2    EHS    1207        1207   
6839               Bacillus_subtilis     BCALM2    EHS    1000        1000   

     Lower bound       NAx  
0           2993  0.000000  
1           2993  0.111111  
2           2993  0.222222  
3           2993  0.333333  
4           2993  0.444444  
...          ...       ...  
6835        1852  0.555556  
6836        1638  0.666667  
6837        1413  0.777778  
6838        1207  0.888889  
6839        1000  1.000000  

[6840 rows x 7 columns]

### Plot data

In [43]:
for sample in sorted(plot_df['Sample'].unique(), key=lambda v: v.upper(), reverse=True):
    print('-' + sample)
    fig=make_subplots(rows=6, cols=2, column_titles=sorted(df['Reference'].unique(), key=lambda v: v.upper(), reverse=True),
                     shared_yaxes=True, shared_xaxes=True, x_title="NAx", y_title="Basepairs")
    row=1
    col=1
    for reference in sorted(plot_df['Reference'].unique(), key=lambda v: v.upper(), reverse=True):
        print('--' + reference)
        i=0
        print(row, col)
        for assembler in sorted(plot_df['Assembler'].unique(), key=lambda v: v.upper(), reverse=True):
            print('---' + assembler)
            showlegend=True if col==1 and row==1 else False
            x = list(plot_df['NAx'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
            if x:
                y=list(plot_df['Average'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
                up_bound=list(plot_df['Upper bound'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
                low_bound=list(plot_df['Lower bound'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
                print(x)
                print(y)
                print(up_bound)
                print(low_bound)

                fig.add_trace(go.Scatter(name=assembler,
                                         x=x,
                                         y=y,
                                         mode='lines',
                                         line=dict(color=COLOURS[i]),
                                         showlegend=showlegend), col=col, row=row)
                fig.add_trace(go.Scatter(name='Upper Bound',
                                         x=x,
                                         y=up_bound,
                                         mode='lines',
                                         marker=dict(color=COLOURS[i]),line=dict(width=0),showlegend=False),col=col, row=row)
                fig.add_trace(go.Scatter(name='Lower Bound',
                                         x=x,
                                         y=low_bound,
                                         marker=dict(color=COLOURS[i]),
                                         line=dict(width=0),
                                         mode='lines',
                                         fillcolor=COLOURS[i],
                                         fill='tonexty',showlegend=False),col=col, row=row)
            i+=1
        if col == 2:
            col = 1
            row += 1
        else:
            col += 1
    fig.update_layout(plot_bgcolor='rgb(255,255,255)', title="{} NAx metric variation".format(sample))
    fig.update_xaxes(showline=True, linewidth=1, linecolor='#DCDCDC', gridcolor='#DCDCDC', rangemode='tozero')
    fig.update_yaxes(showline=True, linewidth=1, linecolor='#DCDCDC', gridcolor='#DCDCDC', range=[0, 1])
    for i in fig['layout']['annotations']:
        i['font']['size'] = 12
    fig.show()
    plot(fig, filename='Plots/Contiguity/NAx/{}.html'.format(sample), auto_open=False)

-LNN
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993]
[2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993]
[2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993, 2993]
---SPAdes
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945]
[2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945]
[2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945, 2945]
---SKESA
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[2893, 2893, 2893, 2893, 289

[90652, 54237, 46114, 33967, 31961, 26629, 20819, 14845, 8131, 1069]
[90652, 54237, 46114, 33967, 31961, 26629, 20819, 14845, 8131, 1069]
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[381853, 366456, 349341, 229307, 208685, 187159, 138115, 103614, 52813, 1078]
[381853, 366456, 349341, 229307, 208685, 187159, 138115, 103614, 52813, 1078]
[381853, 366456, 349341, 229307, 208685, 187159, 138115, 103614, 52813, 1078]
---SPAdes
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[484559, 245391, 209422, 155150, 112027, 88968, 84171, 58920, 39036, 1131]
[484559, 245391, 209422, 155150, 112027, 88968, 84171, 58920, 39036, 1131]
[484559, 245391, 209422, 155150, 112027, 88968, 84171, 58920, 39036,

[110043, 110043, 110043, 110043, 110043, 110043, 110043, 110043, 110043, 110043]
[110043, 110043, 110043, 110043, 110043, 110043, 110043, 110043, 110043, 110043]
---MEGAHIT
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[53216, 53216, 53216, 53216, 53216, 28353, 28353, 26610, 26610, 26610]
[53216, 53216, 53216, 53216, 53216, 28353, 28353, 26610, 26610, 26610]
[53216, 53216, 53216, 53216, 53216, 28353, 28353, 26610, 26610, 26610]
---IDBA-UD
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[53127, 53127, 53127, 53127, 53127, 28766, 28766, 26526, 26526, 26526]
[53127, 53127, 53127, 53127, 53127, 28766, 28766, 26526, 26526, 26526]
[53127, 53127, 53127, 53127, 53127, 28766, 28766, 26526, 26526, 26526]
---GATBMiniaPipeline
[0.0, 0.1111111111111111, 0

[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[18307, 18307, 13850, 8675, 8650, 7326, 5916, 4928, 4006, 1166]
[18307, 18307, 13850, 8675, 8650, 7326, 5916, 4928, 4006, 1166]
[18307, 18307, 13850, 8675, 8650, 7326, 5916, 4928, 4006, 1166]
---MINIA
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[136276, 124837, 110074, 98666, 73760, 64980, 52285, 34762, 22993, 1012]
[136276, 124837, 110074, 98666, 73760, 64980, 52285, 34762, 22993, 1012]
[136276, 124837, 110074, 98666, 73760, 64980, 52285, 34762, 22993, 1012]
---metaSPAdes
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[1032828, 1032828, 1032828, 551839, 315046, 269391, 2

-LHS
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
---SPAdes
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
---SKESA
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
---MINIA
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 

...

[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[130628, 60508, 54893, 46840, 35624, 29167, 23032, 16589, 9773, 1067]
[130628, 60508, 54893, 46840, 35624, 29167, 23032, 16589, 9773, 1067]
[130628, 60508, 54893, 46840, 35624, 29167, 23032, 16589, 9773, 1067]
---Unicycler
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[882626, 882626, 882626, 376042, 376042, 336270, 234872, 179344, 105394, 1048]
[882626, 882626, 882626, 376042, 376042, 336270, 234872, 179344, 105394, 1048]
[882626, 882626, 882626, 376042, 376042, 336270, 234872, 179344, 105394, 1048]
---SPAdes
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[753751, 753751, 

-EHS
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
---Unicycler
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169]
[1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169]
[1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169, 1169]
---SPAdes
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
---SKESA
[0.0, 0.1111111111111111,

[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[461298, 461298, 318001, 290309, 280189, 278993, 174716, 165886, 107773, 1243]
[461298, 461298, 318001, 290309, 280189, 278993, 174716, 165886, 107773, 1243]
[461298, 461298, 318001, 290309, 280189, 278993, 174716, 165886, 107773, 1243]
---SKESA
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[130674, 107847, 75343, 62144, 48709, 41862, 34021, 31524, 17848, 1057]
[130674, 107847, 75343, 62144, 48709, 41862, 34021, 31524, 17848, 1057]
[130674, 107847, 75343, 62144, 48709, 41862, 34021, 31524, 17848, 1057]
---MINIA
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[90652, 54237, 4

[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[161810, 97169, 87316, 54651, 46367, 37618, 29781, 22848, 13596, 1056]
[161810, 97169, 87316, 54651, 46367, 37618, 29781, 22848, 13596, 1056]
[161810, 97169, 87316, 54651, 46367, 37618, 29781, 22848, 13596, 1056]
---Unicycler
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[728300, 728300, 728300, 542499, 474609, 474609, 254431, 145354, 114813, 1131]
[728300, 728300, 728300, 542499, 474609, 474609, 254431, 145354, 114813, 1131]
[728300, 728300, 728300, 542499, 474609, 474609, 254431, 145354, 114813, 1131]
---SPAdes
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[728441, 72844

[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[724374, 724374, 724374, 267958, 238501, 235280, 157734, 105463, 46940, 1097]
[724374, 724374, 724374, 267958, 238501, 235280, 157734, 105463, 46940, 1097]
[724374, 724374, 724374, 267958, 238501, 235280, 157734, 105463, 46940, 1097]
---IDBA-UD
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1.0]
[443329, 443329, 267874, 195054, 118897, 96171, 69129, 55514, 30256, 1000]
[443329, 443329, 267874, 195054, 118897, 96171, 69129, 55514, 30256, 1000]
[443329, 443329, 267874, 195054, 118897, 96171, 69129, 55514, 30256, 1000]
---GATBMiniaPipeline
[0.0, 0.1111111111111111, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444, 0.5555555555555556, 0.6666666666666666, 0.7777777777777777, 0.8888888888888888, 1

## NGx Metric

### Load data

In [44]:
_files = glob.glob('../Results/*/results/*/stats/*ngx.csv')

df_list = []
for f in _files:
    run = f.split('/')[-5]
    sample = f.split('/')[-3]
    assembler = f.split('/')[-1].split('_')[1]
    df = pd.read_csv(f)
    df['run'] = run
    df['Sample'] = sample
    df['Assembler'] = assembler
    df_list.append(df)

df = pd.concat(df_list)
df['distribution'] = np.where(df['Sample'].isin(log_distributed), 'Log', 'Even')
df

Unnamed: 0                       Reference          Assembler       NGx  \
0             0               Bacillus_subtilis             BCALM2  0.000000   
1             1               Bacillus_subtilis             BCALM2  0.111111   
2             2               Bacillus_subtilis             BCALM2  0.222222   
3             3               Bacillus_subtilis             BCALM2  0.333333   
4             4               Bacillus_subtilis             BCALM2  0.444444   
..          ...                             ...                ...       ...   
115         115  Staphylococcus_aureus_plasmid3  GATBMiniaPipeline  0.555556   
116         116  Staphylococcus_aureus_plasmid3  GATBMiniaPipeline  0.666667   
117         117  Staphylococcus_aureus_plasmid3  GATBMiniaPipeline  0.777778   
118         118  Staphylococcus_aureus_plasmid3  GATBMiniaPipeline  0.888889   
119         119  Staphylococcus_aureus_plasmid3  GATBMiniaPipeline  1.000000   

     Basepairs   run      Sample distribution  
0       136276  run1         LNN          Log  
1       124837  run1         LNN          Log  
2        99700  run1         LNN          Log  
3        92807  run1         LNN          Log  
4        71660  run1         LNN          Log  
..         ...   ...         ...          ...  
115       3162  run2  ERR2984773         Even  
116       3162  run2  ERR2984773         Even  
117       3162  run2  ERR2984773         Even  
118       3162  run2  ERR2984773         Even  
119       3162  run2  ERR2984773         Even  

[20520 rows x 8 columns]

### Create Average, Upper bound and Lower bound variables for plot

In [45]:
plot_df = pd.DataFrame(columns=['Reference', 'Assembler', 'Sample', "Average", "Upper bound", "Lower bound", 'NGx'])

for sample in sorted(df['Sample'].unique(), key=lambda v: v.upper(), reverse=True):
    for reference in sorted(df['Reference'].unique(), key=lambda v: v.upper(), reverse=True):
        for assembler in sorted(df['Assembler'].unique(), key=lambda v: v.upper(), reverse=True):
            for x in df['NGx'].unique():
                contigs = list(df['Basepairs'][(df['Assembler'] == assembler) & (df['Reference'] == reference) & (df['Sample'] == sample) & (df['NGx'] == x)])
                if contigs:
                    avg = mean(contigs) if len(set(contigs)) > 1 else contigs[0]
                    upper_bound = max(contigs)
                    lower_bound = min(contigs)
                    plot_df = plot_df.append({'Reference':reference, 'Assembler': assembler, 'Sample': sample, "Average": avg, "Upper bound": upper_bound, "Lower bound": lower_bound, 'NGx': x}, ignore_index=True)

plot_df

Reference  Assembler Sample Average Upper bound  \
0     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
1     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
2     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
3     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
4     Staphylococcus_aureus_plasmid3  Unicycler    LNN    2993        2993   
...                              ...        ...    ...     ...         ...   
6835               Bacillus_subtilis     BCALM2    EHS    1361        1361   
6836               Bacillus_subtilis     BCALM2    EHS    1058        1058   
6837               Bacillus_subtilis     BCALM2    EHS       0           0   
6838               Bacillus_subtilis     BCALM2    EHS       0           0   
6839               Bacillus_subtilis     BCALM2    EHS       0           0   

     Lower bound       NGx  
0           2993  0.000000  
1           2993  0.111111  
2           2993  0.222222  
3           2993  0.333333  
4           2993  0.444444  
...          ...       ...  
6835        1361  0.555556  
6836        1058  0.666667  
6837           0  0.777778  
6838           0  0.888889  
6839           0  1.000000  

[6840 rows x 7 columns]

### Plot data

In [46]:
for sample in sorted(plot_df['Sample'].unique(), key=lambda v: v.upper(), reverse=True):
    print('-' + sample)
    fig=make_subplots(rows=6, cols=2, column_titles=sorted(df['Reference'].unique(), key=lambda v: v.upper(), reverse=True),
                     shared_yaxes=True, shared_xaxes=True, x_title="NGx", y_title="Basepairs")
    row=1
    col=1
    for reference in sorted(plot_df['Reference'].unique(), key=lambda v: v.upper(), reverse=True):
        print('--' + reference)
        i=0
        print(row, col)
        for assembler in sorted(plot_df['Assembler'].unique(), key=lambda v: v.upper(), reverse=True):
            print('---' + assembler)
            showlegend=True if col==1 and row==1 else False
            x = list(plot_df['NGx'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
            if x:
                y=list(plot_df['Average'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
                up_bound=list(plot_df['Upper bound'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])
                low_bound=list(plot_df['Lower bound'][(plot_df['Assembler'] == assembler) & (plot_df['Reference'] == reference) & (plot_df['Sample'] == sample)])

                fig.add_trace(go.Scatter(name=assembler,
                                         x=x,
                                         y=y,
                                         mode='lines',
                                         line=dict(color=COLOURS[i]),
                                         showlegend=showlegend), col=col, row=row)
                fig.add_trace(go.Scatter(name='Upper Bound',
                                         x=x,
                                         y=up_bound,
                                         mode='lines',
                                         marker=dict(color=COLOURS[i]),line=dict(width=0),showlegend=False),col=col, row=row)
                fig.add_trace(go.Scatter(name='Lower Bound',
                                         x=x,
                                         y=low_bound,
                                         marker=dict(color=COLOURS[i]),
                                         line=dict(width=0),
                                         mode='lines',
                                         fillcolor=COLOURS[i],
                                         fill='tonexty',showlegend=False),col=col, row=row)
            i+=1
        if col == 2:
            col = 1
            row += 1
        else:
            col += 1
    fig.update_layout(plot_bgcolor='rgb(255,255,255)', title="{} NGx metric variation".format(sample))
    fig.update_xaxes(showline=True, linewidth=1, linecolor='#DCDCDC', gridcolor='#DCDCDC', rangemode='tozero')
    fig.update_yaxes(showline=True, linewidth=1, linecolor='#DCDCDC', gridcolor='#DCDCDC', range=[0, 1])
    for i in fig['layout']['annotations']:
        i['font']['size'] = 12
    fig.show()
    plot(fig, filename='Plots/Contiguity/NGx/{}.html'.format(sample), auto_open=False)

-LNN
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---VelvetO

-LHS
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---VelvetO

-ERR2984773
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---

-ERR2935805
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---

-ENN
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---VelvetO

-EHS
--Staphylococcus_aureus_plasmid3
1 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid2
1 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus_plasmid1
2 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Staphylococcus_aureus
2 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Salmonella_enterica
3 1
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Pseudomonas_aeruginosa
3 2
---VelvetOptimizer
---Unicycler
---SPAdes
---SKESA
---MINIA
---metaSPAdes
---MEGAHIT
---IDBA-UD
---GATBMiniaPipeline
---BCALM2
--Listeria_monocytogenes
4 1
---VelvetO